In [25]:
import enum
import glob
import os
from hashlib import new
from pathlib import Path
import time
from itertools import product

import functools

import numpy as np
import pandas as pd
import scipy
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from snorkel.labeling.model import LabelModel as LMsnorkel
from snorkel.labeling.model import MajorityLabelVoter

from sklearn.model_selection import train_test_split
import itertools
import ast

In [26]:
import joblib
import json
import collections

In [27]:
from sklearn.exceptions import UndefinedMetricWarning

def warn(*args, **kwargs):
    pass
import warnings
warnings.warn = warn

In [28]:
def list2Nested(l, nested_length):
    return [l[i:i+nested_length] for i in range(0, len(l), nested_length)]

In [29]:
labelModel_mapper_LF = {1:1, -1:0, 0:-1}

In [186]:
import LMutils

train_file = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v4/gt/train_ebm_labels_tui_pio3.tsv'
training_data = pd.read_csv(train_file, sep='\t', header=0)

ebm_test_file = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v4/gt/test_ebm_labels_tui_pio3.tsv'
test_ebm_data = pd.read_csv(ebm_test_file, sep='\t', header=0)
test_ebm_data.rename( columns={'Unnamed: 0':'series'}, inplace=True )

physio_test_file = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v4/gt/test_physio_labels_tui_pio3.tsv'
test_physio_data = pd.read_csv(physio_test_file, sep='\t', header=0)
test_physio_data.rename( columns={'Unnamed: 0':'series'}, inplace=True )

ebm_test_corrected_file = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v4/gt/test_ebm_correctedlabels_tui_pio3.tsv'
test_ebm_corrected_data = pd.read_csv(ebm_test_corrected_file, sep='\t', header=0)
test_ebm_corrected_data.rename( columns={'Unnamed: 0':'series'}, inplace=True )

In [187]:
def flatten_df(df):

    df_series = [ index for index, value in df.tokens.items() for word in ast.literal_eval(value) ]
    df_tokens = [ word for index, value in df.tokens.items() for word in ast.literal_eval(value) ]
    df_pos = [ word for index, value in df.pos.items() for word in ast.literal_eval(value) ]
    df_offsets = [ word for index, value in df.offsets.items() for word in ast.literal_eval(value) ]


    df_p = [ int(lab) for index, value in df.p.items() for lab in ast.literal_eval(value) ]
    df_p_fine = [ int(lab) for index, value in df.p_f.items() for lab in ast.literal_eval(value) ]
    df_i = [ int(lab) for index, value in df.i.items() for lab in ast.literal_eval(value) ]
    df_i_fine = [ int(lab) for index, value in df.i_f.items() for lab in ast.literal_eval(value) ]
    df_o = [ int(lab) for index, value in df.o.items() for lab in ast.literal_eval(value) ]
    df_o_fine = [ int(lab) for index, value in df.o_f.items() for lab in ast.literal_eval(value) ]
    
    df_flattened = pd.DataFrame({ 'series': df_series,
                        'tokens' : df_tokens,
                        'offsets': df_offsets,
                        'pos': df_pos,
                        'p' : df_p,
                        'i' : df_i,
                        'o' : df_o,
                        'p_f' : df_p_fine,
                        'i_f' : df_i_fine,
                        'o_f' : df_o_fine })
    
    return df_flattened

In [188]:
# Flatten the dataframes (currently only the training dataframe and test ebm dataframe with corrected labels can be flattened)
data_df = flatten_df(training_data)
test_ebm_data = flatten_df(test_ebm_data)
test_ebm_corr_df = flatten_df(test_ebm_corrected_data)

In [245]:
series = [
    data_df.series.to_numpy() ,
    test_ebm_data.series.to_numpy() ,
    test_physio_data.series.to_numpy(),   
    test_ebm_corr_df.series.to_numpy()
]


sents = [
    data_df.tokens.to_numpy() ,
    test_ebm_data.tokens.to_numpy() ,
    test_physio_data.tokens.to_numpy(),   
    test_ebm_corr_df.tokens.to_numpy()    
]


part_of_speech = [
    data_df.pos.to_numpy() ,
    test_ebm_data.pos.to_numpy() ,
    test_physio_data.pos.to_numpy(),   
    test_ebm_corr_df.pos.to_numpy()     
]


offsets = [
    data_df.offsets.to_numpy() ,
    test_ebm_data.offsets.to_numpy() ,
    test_physio_data.offsets.to_numpy(),   
    test_ebm_corr_df.offsets.to_numpy() 
]


Y_p = [
    data_df.p.to_numpy() , # 0 -7
    data_df.p_f.to_numpy() , # 1 -6
    test_ebm_data.p.to_numpy() , # 2 -5
    test_ebm_data.p_f.to_numpy() , # 3 -4
    test_physio_data.p.to_numpy(),  # 4 -3
    test_ebm_corr_df.p.to_numpy(),   # 5 -2
    test_ebm_corr_df.p_f.to_numpy() # 6 -1
]


Y_i = [
    data_df.i.to_numpy() , # 0 -7
    data_df.i_f.to_numpy() , # 1 -6
    test_ebm_data.i.to_numpy() , # 2 -5
    test_ebm_data.i_f.to_numpy() , # 3 -4
    test_physio_data.i.to_numpy(),  # 4 -3
    test_ebm_corr_df.i.to_numpy(),   # 5 -2
    test_ebm_corr_df.i_f.to_numpy() # 6 -1
]


Y_o = [
    data_df.o.to_numpy() ,
    data_df.o_f.to_numpy() ,
    test_ebm_data.o.to_numpy() ,
    test_physio_data.o.to_numpy() 
]

In [190]:
# Write data for error analysis

error_analysis_ebm_p = pd.DataFrame({'tokens' : test_ebm_data.tokens,
                                'participant' : test_ebm_data.p,
                                'participant_fine' : test_ebm_data.p_f }, 
                                columns=['tokens','participant', 'participant_fine'])

#error_analysis_ebm_p.to_csv (r'/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/error_analysis/test_ebmgold_p', index = None, header=True) 

In [191]:
# Write data for error analysis

error_analysis_ebmcorr_p = pd.DataFrame({'tokens' : test_ebm_corr_df.tokens,
                                'participant' : test_ebm_corr_df.p,
                                'participant_fine' : test_ebm_corr_df.p_f }, 
                                columns=['tokens','participant', 'participant_fine'])

#error_analysis_ebmcorr_p.to_csv (r'/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/error_analysis/test_ebmgoldcorr_p', index = None, header=True) 

In [192]:
def df_to_list(data_column):
    return [ word for index, value in data_column.items() for word in ast.literal_eval(value) ]

In [193]:
def df_to_array(data_column):
    return np.array( [ word for index, value in data_column.items() for word in ast.literal_eval(value) ] )

In [194]:
def dict_to_array(label_column):
    return np.array( [ labelModel_mapper_LF[int(lab)] for index, value in label_column.items() for k, lab in ast.literal_eval(value).items() ] )

In [225]:
def get_lfs(indir):
    
    pathlist = Path(indir).glob('**/*.tsv')

    tokens = ''

    lfs = dict()
    lfs_lm = dict()

    for counter, file in enumerate(pathlist):

        k = str( file ).split('/v4/')[-1].replace('.tsv', '').replace('/', '_')
        mypath = Path(file)
        if mypath.stat().st_size != 0:
            data = pd.read_csv(file, sep='\t', header=0)

            data_tokens = data.tokens
            if len(tokens) < 5:
                tokens = df_to_array(data_tokens)

            data_labels = data.labels
            #print(len(data_labels))
            labels = dict_to_array(data_labels)
            #print(len(labels))
            if len(labels) != len(tokens):
                print(k, len(labels) , len(tokens) )
            #assert len(labels) == len(tokens)
            lfs[k] = labels


    print( 'Total number of tokens in validation set: ', len(tokens) )
    print( 'Total number of LFs in the dictionary', len(lfs) )
    
    return lfs

In [226]:
indir = '/mnt/nas2/results/Results/systematicReview/distant_pico/training_ebm_candidate_generation/v4'
train_ebm_lfs = get_lfs(indir)

Total number of tokens in validation set:  1303169
Total number of LFs in the dictionary 843


In [227]:
indir_test_ebm_corr = '/mnt/nas2/results/Results/systematicReview/distant_pico/test_ebm_anjani_candidate_generation/v4'
test_ebm_corr_lfs = get_lfs(indir_test_ebm_corr)

Total number of tokens in validation set:  52582
Total number of LFs in the dictionary 843


In [228]:
indir_test_ebm = '/mnt/nas2/results/Results/systematicReview/distant_pico/test_ebm_candidate_generation/v4'
test_ebm_lfs = get_lfs(indir_test_ebm)

Total number of tokens in validation set:  51784
Total number of LFs in the dictionary 843


In [229]:
# Remove the annotations where there are no positive labels
print('Dropping no positive label LFs')

def drop_nopositive(lfs_d):
    
    dropped_no_positives = dict()

    for k, v in lfs_d.items():

        if len(set(v)) < 3:
            if 1 in list(set(v)):
                dropped_no_positives[k] = v
        else:
            dropped_no_positives[k] = v
            
    return dropped_no_positives

#lfs_dropped = drop_nopositive(lfs)
#print('Number of LFs: ', len(lfs_dropped))
#lfs_ebm_corr_dropped = drop_nopositive(test_ebm_corr_lfs)
#print('Number of LFs: ', len(lfs_ebm_corr_dropped))

Dropping no positive label LFs


In [230]:
def lf_levels(umls_d:dict, pattern:str, picos:str):

    umls_level = dict()

    for key, value in umls_d.items():   # iter on both keys and values
        search_pattern = pattern + picos
        if key.startswith(search_pattern):
            k = str(key).split('_')[-1]
            umls_level[ k ] = value

    return umls_level


# Level 1: UMLS
umls_p = [
    lf_levels(train_ebm_lfs, name, 'P') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_p_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'P') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_p_testebm = [
    lf_levels(test_ebm_lfs, name, 'P') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

# ------------------------------------------------------------------------

umls_i = [
    lf_levels(train_ebm_lfs, name, 'I') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_i_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'I') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_i_testebm = [
    lf_levels(test_ebm_lfs, name, 'I') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

# ------------------------------------------------------------------------

umls_o = [
    lf_levels(train_ebm_lfs, name, 'O') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_o_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'O') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

umls_o_testebm = [
    lf_levels(test_ebm_lfs, name, 'O') 
    for i, name in enumerate(['UMLS_direct_', 'UMLS_fuzzy_'])
]

# ------------------------------------------------------------------------
# ------------------------------------------------------------------------


# Level 2: non UMLS
nonumls_p = [
    lf_levels(train_ebm_lfs, name, 'P') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_p_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'P') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_p_testebm = [
    lf_levels(test_ebm_lfs, name, 'P') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

# ------------------------------------------------------------------------


nonumls_i = [
    lf_levels(train_ebm_lfs, name, 'I') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_i_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'I') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_i_testebm = [
    lf_levels(test_ebm_lfs, name, 'I') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

# ------------------------------------------------------------------------

nonumls_o = [
    lf_levels(train_ebm_lfs, name, 'O') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_o_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'O') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

nonumls_o_testebm = [
    lf_levels(test_ebm_lfs, name, 'O') 
    for i, name in enumerate(['nonUMLS_direct_', 'nonUMLS_fuzzy_'])
]

# ------------------------------------------------------------------------
# ------------------------------------------------------------------------

# Level 3: DS
ds_p = [
    lf_levels(train_ebm_lfs, name, 'P') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_p_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'P') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_p_testebm = [
    lf_levels(test_ebm_lfs, name, 'P') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]


# ------------------------------------------------------------------------

ds_i = [
    lf_levels(train_ebm_lfs, name, 'I') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_i_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'I') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_i_testebm = [
    lf_levels(test_ebm_lfs, name, 'I') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

# ------------------------------------------------------------------------

ds_o = [
    lf_levels(train_ebm_lfs, name, 'O') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_o_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'O') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

ds_o_testebm = [
    lf_levels(test_ebm_lfs, name, 'O') 
    for i, name in enumerate(['ds_direct_', 'ds_fuzzy_'])
]

# ------------------------------------------------------------------------
# ------------------------------------------------------------------------


# Level 4: dictionary, rules, heuristics
heur_p = [
    lf_levels(train_ebm_lfs, name, 'P') 
    for i, name in enumerate(['heuristics_direct_'])
]

heur_p_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'P') 
    for i, name in enumerate(['heuristics_direct_'])
]

heur_p_testebm = [
    lf_levels(test_ebm_lfs, name, 'P') 
    for i, name in enumerate(['heuristics_direct_'])
]

# ------------------------------------------------------------------------

heur_i = [
    lf_levels(train_ebm_lfs, name, 'I') 
    for i, name in enumerate(['heuristics_direct_'])
]

heur_i_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'I') 
    for i, name in enumerate(['heuristics_direct_'])
]

heur_i_testebm = [
    lf_levels(test_ebm_lfs, name, 'I') 
    for i, name in enumerate(['heuristics_direct_'])
]

# ------------------------------------------------------------------------

heur_o = [
    lf_levels(train_ebm_lfs, name, 'O') 
    for i, name in enumerate(['heuristics_direct_'])
]

heur_o_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'O') 
    for i, name in enumerate(['heuristics_direct_'])
]


heur_o_testebm = [
    lf_levels(test_ebm_lfs, name, 'O') 
    for i, name in enumerate(['heuristics_direct_'])
]

# ------------------------------------------------------------------------
# ------------------------------------------------------------------------


dict_p = [
    lf_levels(train_ebm_lfs, name, 'P') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_p_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'P') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_p_testebm = [
    lf_levels(test_ebm_lfs, name, 'P') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

# ------------------------------------------------------------------------

dict_i = [
    lf_levels(train_ebm_lfs, name, 'I') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_i_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'I') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_i_testebm = [
    lf_levels(test_ebm_lfs, name, 'I') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

# ------------------------------------------------------------------------

dict_o = [
    lf_levels(train_ebm_lfs, name, 'O') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_o_testcorrected = [
    lf_levels(test_ebm_corr_lfs, name, 'O') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

dict_o_testebm = [
    lf_levels(test_ebm_lfs, name, 'O') 
    for i, name in enumerate(['dictionary_direct_', 'dictionary_fuzzy_'])
]

In [231]:
# Participant data

train_candidates = [umls_p[1], nonumls_p[1], ds_p[1], dict_p[1], heur_p[0]]
test_ebm_corr_candidates = [umls_p_testcorrected[1], nonumls_p_testcorrected[1], ds_p_testcorrected[1], dict_p_testcorrected[1], heur_p_testcorrected[0]]
test_ebm_candidates = [umls_p_testebm[1], nonumls_p_testebm[1], ds_p_testebm[1], dict_p_testebm[1], heur_p_testebm[0]]

In [232]:
# Intervention data

train_i_candidates = [umls_i[1], nonumls_i[1], ds_i[1], dict_i[1], heur_i[0]]
test_i_ebm_corr_candidates = [umls_i_testcorrected[1], nonumls_i_testcorrected[1], ds_i_testcorrected[1], dict_i_testcorrected[1], heur_i_testcorrected[0]]
test_i_ebm_candidates = [umls_i_testebm[1], nonumls_i_testebm[1], ds_i_testebm[1], dict_i_testebm[1], heur_i_testebm[0]]

In [233]:
def getLen(lf):
    for l in lf:
        for k,v in l.items():
            print(len(v))
            
#getLen(umls_i) 
#getLen(nonumls_i) 

In [234]:
# Fetch UMLS ranks

sum_lf_p = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v3/summaries/lf_p_summary_tuipio3_train.csv'
sum_lf_i = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v3/summaries/lf_i_summary_tuipio3_train.csv'
sum_lf_o = '/mnt/nas2/results/Results/systematicReview/distant_pico/EBM_PICO_GT/v3/summaries/lf_o_summary_tuipio3_train.csv'


def fetchRank(sum_lf_d, pattern, picos: str, drop_nopos: bool):
    
    drop_nopos_keys = []
    for k,v in train_ebm_lfs.items():
        query = '_'+picos+'_'
        if query in str(k):
            key = str(k).split('_lf_')[-1]
            drop_nopos_keys.append(key)
    
    ranked_umls_coverage = dict()    
    umls_coverage_ = dict()
    
    data=pd.read_csv(sum_lf_d, sep='\t')
    
    for index, row in data.iterrows():
        if row[0].startswith(pattern):
            umls_coverage_[row[0]] = row[3]
    
    umls_coverage_sorted = sorted(umls_coverage_.items(), key=lambda x: x[1], reverse=True)
    
    for i in umls_coverage_sorted:
        k = str(i[0]).split('_')[-1]
        if drop_nopos == False:
            ranked_umls_coverage[k] = i[1]
        else:
            if k in drop_nopos_keys:
                ranked_umls_coverage[k] = i[1]

    return ranked_umls_coverage


# fuzzy UMLS
ranksorted_p_umls_fuzzy = fetchRank(sum_lf_p, 'UMLS_fuzzy_', picos='P', drop_nopos = False)
ranksorted_i_umls_fuzzy = fetchRank(sum_lf_i, 'UMLS_fuzzy_', picos='I', drop_nopos = False)
ranksorted_o_umls_fuzzy = fetchRank(sum_lf_o, 'UMLS_fuzzy_', picos='O', drop_nopos = False)


# direct UMLS
ranksorted_p_umls_direct = fetchRank(sum_lf_p, 'UMLS_direct_', picos='P', drop_nopos = False)
ranksorted_i_umls_direct = fetchRank(sum_lf_i, 'UMLS_direct_', picos='I', drop_nopos = False)
ranksorted_o_umls_direct = fetchRank(sum_lf_o, 'UMLS_direct_', picos='O', drop_nopos = False)

proper_coverage_p = '/mnt/nas2/results/Results/systematicReview/distant_pico/coverage_results/participant_UMLS_v3_coverage.json'

with open(proper_coverage_p, 'r') as rf:
    data = json.load(rf)
 
    for k, v in data.items():
        if k in ranksorted_p_umls_fuzzy:
            ranksorted_p_umls_fuzzy[k] = data[k]
            
ranksorted_coverage_p_umls_fuzzy = sorted(ranksorted_p_umls_fuzzy.items(), key=lambda x: x[1], reverse=True)
ranksorted_coverage_p_umls_fuzzy = dict(ranksorted_coverage_p_umls_fuzzy)


proper_coverage_i = '/mnt/nas2/results/Results/systematicReview/distant_pico/coverage_results/intervention_UMLS_v3_coverage.json'

with open(proper_coverage_i, 'r') as rf:
    data = json.load(rf)
 
    for k, v in data.items():
        if k in ranksorted_i_umls_fuzzy:
            ranksorted_i_umls_fuzzy[k] = data[k]
            
ranksorted_coverage_i_umls_fuzzy = sorted(ranksorted_i_umls_fuzzy.items(), key=lambda x: x[1], reverse=True)
ranksorted_coverage_i_umls_fuzzy = dict(ranksorted_coverage_i_umls_fuzzy)

In [235]:
# Partition LF's

def partitionLFs(umls_d):
    
    keys = list(umls_d.keys())

    partitioned_lfs = [ ]
    
    for i in range( 0, len(keys) ):

        if i == 0 or i == len(keys):
            if i == 0:
                partitioned_lfs.append( [keys] )
            if i ==len(keys):
                temp3 = list2Nested(keys, 1)
                partitioned_lfs.append( temp3 )
        else:
            temp1, temp2 = keys[:i] , keys[i:]
            temp3 = list2Nested( keys[:i], 1)
            temp3.append( keys[i:] )
            partitioned_lfs.append( temp3 )
    
    return partitioned_lfs


partitioned_p_umls_fuzzy = partitionLFs(ranksorted_coverage_p_umls_fuzzy)
partitioned_i_umls_fuzzy = partitionLFs(ranksorted_coverage_i_umls_fuzzy)
partitioned_o_umls_fuzzy = partitionLFs(ranksorted_o_umls_fuzzy)

partitioned_p_umls_direct = partitionLFs(ranksorted_p_umls_direct)
partitioned_i_umls_direct = partitionLFs(ranksorted_i_umls_direct)
partitioned_o_umls_direct = partitionLFs(ranksorted_o_umls_direct)

In [236]:
exp_level = ['UMLS', 'UMLS_Ontology', 'UMLS_Ontology_Rules']

In [237]:
param_grid = {
    'lr': [0.001, 0.0001],
    'l2': [0.001, 0.0001],
    'n_epochs': [50, 100, 200, 600, 700, 1000, 2000],
    'prec_init': [0.6, 0.7, 0.8, 0.9],
    'optimizer': ["adamax", "adam", "sgd"],
    'lr_scheduler': ['constant'],
}

In [238]:
def sample_param_grid(param_grid, seed):
    """ Sample parameter grid
    :param param_grid:
    :param seed:
    :return:
    """
    rstate = np.random.get_state()
    np.random.seed(seed)
    params = list(product(*[param_grid[name] for name in param_grid]))
    np.random.shuffle(params)
    np.random.set_state(rstate)
    return params

In [239]:
def compare(s, t):
    return sorted(s) == sorted(t)

def getLFs(partition:list, umls_d:dict, seed_len:int):

    all_lfs_combined = []
    
    for lf in partition: # for each lf in a partition
        
        combine_here = [0] * seed_len

        for sab in lf:
            new_a = list(umls_d[sab])
            old_a = combine_here
            temp_a = []
            
            for o_a, n_a in zip(old_a, new_a):
                               
                if compare([o_a, n_a] ,[-1, 1]) == True:
                    replace_a = max( o_a, n_a )
                    temp_a.append( replace_a )
                    
                elif compare([o_a, n_a] ,[0, 1]) == True:
                    replace_a = max( o_a, n_a )
                    temp_a.append( replace_a )
                    
                elif compare([o_a, n_a] ,[-1, 0]) == True:
                    replace_a = min( o_a, n_a )
                    temp_a.append( replace_a )
                else:
                    temp_a.append( o_a )

            combine_here = temp_a

        all_lfs_combined.append( combine_here )

    return all_lfs_combined

In [240]:
def grid_search(model_class,
                model_class_init,
                param_grid,
                train=None,
                dev=None,
                other_train=None,
                n_model_search=5,
                val_metric='f1_macro',
                seed=1234,
                checkpoint_gt_mv=False,
                tag_fmt_ckpnt='IO'):
    
    
    """Simple grid search helper function
    Parameters
    ----------
    model_class
    model_class_init
    param_grid
    train
    dev
    n_model_search
    val_metric
    seed

    Returns
    -------
    """
    
    L_train, Y_train = train
    L_dev, Y_dev = dev

    # sample configs
    params = sample_param_grid(param_grid, seed)[:n_model_search]

    defaults = {'seed': seed}
    best_score, best_config = 0.0, None
    print(f"Grid search over {len(params)} configs")

    for i, config in enumerate(params):
        print(f'[{i}] Label Model')
        config = dict(zip(param_grid.keys(), config))
        config.update({param: value for param, value in defaults.items() if param not in config})

        model = model_class(**model_class_init)
        model.fit(L_train, Y_dev, **config)
        
        y_pred = model.predict(L_dev)
        
        if tag_fmt_ckpnt == 'IO':
            y_gold = np.array([0 if y == 0 else 1 for y in Y_dev])
        else:
            y_gold = Y_dev
            
            
        if -1 in y_pred:
            print("Label model predicted -1 (TODO: this happens inconsistently)")
            continue
            
        # use internal label model scorer to score the prediction
        metrics = model.score(L=L_dev,
                              Y=y_gold,
                              metrics=['accuracy', 'precision', 'recall', 'f1', 'f1_macro'],
                              tie_break_policy='random')
        
    
        # compare learned model against MV on same labeled dev set
        # skip if LM less than MV
        if checkpoint_gt_mv:
            mv_metrics = model.score(L=L_dev,
                                  Y=y_gold,
                                  metrics=['accuracy', 'precision', 'recall', 'f1', 'f1_macro'],
                                  tie_break_policy='random')

            if metrics[val_metric] < mv_metrics[val_metric]:
                continue
                
        if not best_score or metrics[val_metric] > best_score[val_metric]:
            print(config)
            best_score = metrics
            best_config = config
            
            # print training set score if we have labeled data
            if np.any(Y_train):
                y_pred = model.predict(L_train)

                if tag_fmt_ckpnt == 'IO':
                    y_gold = np.array([0 if y == 0 else 1 for y in Y_train])
                else:
                    y_gold = Y_train

                metrics = model.score(L=L_train,
                                      Y=y_gold,
                                      metrics=['accuracy', 'precision', 'recall', 'f1', 'f1_macro'],
                                      tie_break_policy='random')

                print('[TRAIN] {}'.format(' | '.join([f'{m}: {v * 100:2.2f}' for m, v in metrics.items()])))

            print('[DEV]   {}'.format(' | '.join([f'{m}: {v * 100:2.2f}' for m, v in best_score.items()])))
            print('-' * 88)
            
            
    # retrain best model
    print('BEST')
    print(best_config)
    model = model_class(**model_class_init)
    
    
    model.fit(L_train, Y_dev, **best_config)
    return model, best_config, best_score

In [241]:
def predict(part, cands, best_model, gt_labels, exp_l):
    
    if exp_l == 'UMLS':
    
        combined_lf = getLFs( part, cands[0], len(gt_labels) )
        assert len(part) == len(combined_lf)
        print( 'Total number of UMLS partitions: ', len(part) )
        
    elif exp_l == 'UMLS_Ontology':
    
        combined_lf = getLFs( part, cands[0], len(gt_labels) )
        assert len(part) == len(combined_lf)
        print( 'Total number of UMLS partitions: ', len(part) )
        combined_lf.extend( list(cands[1].values()) ) # Combine with level 2
        combined_lf.extend( list(cands[2].values()) ) # Combine with level 3
        combined_lf.extend( list(cands[3].values()) ) # Combine with level 4
        
    elif exp_l == 'UMLS_Ontology_Rules':

        combined_lf = getLFs( part, cands[0], len(gt_labels) )
        assert len(part) == len(combined_lf)
        print( 'Total number of UMLS partitions: ', len(part) )
        combined_lf.extend( list(cands[1].values()) ) # Combine with level 2
        combined_lf.extend( list(cands[2].values()) ) # Combine with level 3
        combined_lf.extend( list(cands[3].values()) ) # Combine with level 4
        combined_lf.extend( list(cands[4].values()) ) # combine with level 4


    L = np.array( combined_lf )
    L = np.transpose(L)
    
    predictions_probablities = best_model.predict_proba(L)
    predictions = best_model.predict(L)
    groundtruth = np.array(gt_labels) 
    groundtruth_ = [1 if x != 0 else x for x in gt_labels] # XXX if "test_ebm_correct"
    groundtruth = np.array(groundtruth_)

    cr = classification_report( groundtruth, predictions )
    print( cr )
    
    return predictions_probablities

In [246]:
def train(partitioned_d_umls, train_cands, test_cands, test_corr_cands, Y_d, picos, paramgrid, mode):
   
    gold_labels = ''
    gold_labels_fine = ''
    
    
    model_class_init = {
        'cardinality': 2, 
        'verbose': True
    }

    num_hyperparams = functools.reduce(lambda x,y:x*y, [len(x) for x in param_grid.values()])
    print("Hyperparamater Search Space:", num_hyperparams)
    n_model_search = 50
    

    '''#########################################################################
    # Choosing the number of LF's from UMLS all
    #########################################################################'''
    
    for l in exp_level:
        print( 'Executing the experiment level: ', l )
        
        best_f1_macro = 0.0
        best_overall_model = ''
        best_overall_config = ''
        best_overall_partition = 0
        overall_L = ''
    
        for i, partition in enumerate(partitioned_d_umls):
        
            #if len(partition) == 2:
            
            if l == 'UMLS' and i < 2:
                continue

            if l == 'UMLS':

                combined_lf = getLFs(partition, train_cands[0], len( data_df.tokens ))
                #combined_lf = combined_lf[2:]  # i>2 (as LM should have at least 3 labeling functions)
                assert len(partition) == len(combined_lf)
                print( 'Total number of UMLS partitions: ', len(partition) )
                
            if l == 'UMLS_Ontology':

                combined_lf = getLFs(partition, train_cands[0], len( data_df.tokens ))
                assert len(partition) == len(combined_lf)
                print( 'Total number of UMLS partitions: ', len(partition) )
                combined_lf.extend( list(train_cands[1].values()) ) # Combine with level 2
                combined_lf.extend( list(train_cands[2].values()) ) # Combine with level 3
                combined_lf.extend( list(train_cands[3].values()) ) # Combine with level 4
            
            if l == 'UMLS_Ontology_Rules':

                combined_lf = getLFs(partition, train_cands[0], len( data_df.tokens ))
                assert len(partition) == len(combined_lf)
                print( 'Total number of UMLS partitions: ', len(partition) )
                combined_lf.extend( list(train_cands[1].values()) ) # Combine with level 2
                combined_lf.extend( list(train_cands[2].values()) ) # Combine with level 3
                combined_lf.extend( list(train_cands[3].values()) ) # Combine with level 4
                combined_lf.extend( list(train_cands[4].values()) ) # combine with level 4


            L = np.array( combined_lf )
            L = np.transpose(L)
            L_train, L_val = train_test_split(L, test_size=0.20, shuffle=False)
            Y_train, Y_val = train_test_split( np.array(Y_d[0]), test_size=0.20, shuffle=False)
            Y_train_fine, Y_val_fine = train_test_split( np.array(Y_d[1]), test_size=0.20, shuffle=False)

            # convert the fine labels to 0 and 1
            Y_train_fine = [1 if x != 0 else x for x in Y_train_fine]
            Y_val_fine = [1 if x != 0 else x for x in Y_val_fine]

            #print( Y_val_fine )


            #Y_train = Y_d[0]
            #Y_val = Y_d[1]
            Y = np.concatenate([Y_train, Y_val])
            Y_fine = np.concatenate([Y_train_fine, Y_val_fine])

            best_model, best_config, best_score = grid_search(LMsnorkel, 
                                                   model_class_init, 
                                                   paramgrid,
                                                   train = (L_train, Y_train_fine),
                                                   dev = (L_val, Y_val_fine),
                                                   n_model_search=n_model_search, 
                                                   val_metric='f1_macro', 
                                                   seed=1234,
                                                   tag_fmt_ckpnt='IO')


            if best_score['f1_macro'] > best_f1_macro:
                best_f1_macro = best_score['f1_macro']
                best_overall_model = best_model
                best_overall_config = best_config
                best_overall_partition = i
                overall_L = L
                gold_labels = Y_d[0]
                gold_labels_fine = Y_d[1]


            print('Best overall macro F1 score: ', best_f1_macro)
            print('Best overall configuration: ', best_overall_config)


        print('Save the best overall model, configuration and partition for this experiment level')
        # Save your model or results
        save_dir = f'/mnt/nas2/results/Results/systematicReview/distant_pico/models/LabelModels/{picos}/v4/{l}'
        filename = 'stpartition_' + str(best_overall_partition+1) + '_epoch_' + str(best_config['n_epochs'])
        joblib.dump(best_overall_model, f'{save_dir}/{filename}.pkl') 
        joblib.dump(best_overall_config, f'{save_dir}/{filename}.json')

        #load your model for further usage
        loaded_best_model = joblib.load(f'{save_dir}/{filename}.pkl')

        # Initialize token predictions here
        token_predictions = dict()

        # Predict on the training set
        for i, partition in enumerate(partitioned_d_umls):

            if i == best_overall_partition:

                # Predict on the test ebm correct set
                test_corr_probas = predict(partition, test_corr_cands, loaded_best_model, Y_d[-2], l) # test ebm correct   

                # Predict on the test ebm set
                test_ebm_probas = predict(partition, test_cands,loaded_best_model, Y_d[-4], l) # test ebm
                test_ebm_probas_coarse = predict(partition, test_cands,loaded_best_model, Y_d[-5], l) # test ebm coarse grained

                # Predict on the training set
                train_probas = predict(partition, train_cands,loaded_best_model, Y_d[-6], l) # train 

                # Write training predictions to file
                # tokens	pos	offsets	labels	true_labels
                train_probas = [list(tp) for tp in train_probas]
                train_probas_series = pd.Series(list(train_probas))
                data_df['labels'] = train_probas_series.values
                
                # Write predictions on the training data to the file
                write_df = data_df.groupby(['series'])[['series', 'tokens', 'pos', 'offsets', 'labels', str(picos), str(picos)+'_f']].agg(list)
                write_file_path = f'/mnt/nas2/results/Results/systematicReview/distant_pico/predictions/LabelModels/{picos}/v4/{l}/{filename}_bestmodel.tsv'
                write_df.to_csv (write_file_path, index = None, sep = '\t', header=True) 

                # Write predictions for the ebm and ebm corrected files
                #token_predictions = dict()
                #for counter, (T, P, Y_d_i, Y_d_i_fine) in enumerate(zip(tokens, predictions, gold_labels, gold_labels_fine)):
                #    token_predictions[counter] = [T, list(P), list(P).index(max(list(P))), str(Y_d_i), str(Y_d_i_fine)]

        #with open(f'{save_dir}/{filename}_results.json', 'w+') as fp:
        #    json.dump(token_predictions, fp)
            
    #return token_predictions

In [185]:
predicted_p = train(partitioned_p_umls_fuzzy, train_candidates, test_ebm_candidates, test_ebm_corr_candidates, Y_p, 'p', paramgrid = param_grid, mode = 'pred')

Hyperparamater Search Space: 336
Executing the experiment level:  UMLS
Total number of UMLS partitions:  3
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.71 | precision: 23.84 | recall: 24.37 | f1: 24.10 | f1_macro: 60.41
[DEV]   accuracy: 93.86 | precision: 22.33 | recall: 25.07 | f1: 23.62 | f1_macro: 60.21
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.43 | precision: 23.35 | recall: 26.45 | f1: 24.81 | f1_macro: 60.69
[DEV]   accuracy: 93.53 | precision: 21.67 | recall: 27.00 | f1: 24.04 | f1_macro: 60.33
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model


Best overall macro F1 score:  0.6033408556079498
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  6
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.49 | precision: 22.97 | recall: 24.98 | f1: 23.93 | f1_macro: 60.27
[DEV]   accuracy: 93.68 | precision: 21.77 | recall: 25.77 | f1: 23.60 | f1_macro: 60.15
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.50 | precision: 23.01 | recall: 24.97 | f1: 23.95 | f1_macro: 60.28
[DEV]   accuracy: 93.69 | precision: 21.83 | recall: 25.78 

Total number of UMLS partitions:  9
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.27 | precision: 22.64 | recall: 26.63 | f1: 24.47 | f1_macro: 60.47
[DEV]   accuracy: 93.46 | precision: 21.83 | recall: 28.08 | f1: 24.56 | f1_macro: 60.57
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.44 | precision: 23.37 | recall: 26.38 | f1: 24.79 | f1_macro: 60.68
[DEV]   accuracy: 93.61 | precision: 22.29 | recall: 27.61 | f1: 24.67 | f1_macro: 60.67
----------------------------------------------------------------------------------------
[7] Label Model
[8] Label Model
[9] La

[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6096994755957679
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UM

[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.44 | precision: 23.35 | recall: 26.30 | f1: 24.74 | f1_macro: 60.65
[DEV]   accuracy: 93.63 | precision: 22.61 | recall: 28.15 | f1: 25.07 | f1_macro: 60.87
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model


...

[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  119
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}


[TRAIN] accuracy: 92.70 | precision: 22.69 | recall: 32.51 | f1: 26.72 | f1_macro: 61.44
[DEV]   accuracy: 92.82 | precision: 21.36 | recall: 33.33 | f1: 26.04 | f1_macro: 61.13
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.62 | precision: 22.52 | recall: 32.87 | f1: 26.73 | f1_macro: 61.42
[DEV]   accuracy: 92.78 | precision: 21.47 | recall: 34.08 | f1: 26.35 | f1_macro: 61.27
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.46 | precision: 22.80 | recal

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.42 | precision: 24.97 | recall: 30.26 | f1: 27.36 | f1_macro: 61.96
[DEV]   accuracy: 93.64 | precision: 23.83 | recall: 30.93 | f1: 26.92 | f1_macro: 61.80
----------------------------------------------------------------------------------------
[12] Label Model
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.78 | precision: 26.35 | recall: 28.87 | f1: 27.55 | f1_macro: 62.15
[DEV]   accuracy: 93.98 | precision: 25.00 | recall: 29.40 | f1: 27.02 | f1_macro: 61.94
----------------------------------------------------------------------------------------
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 

[TRAIN] accuracy: 93.21 | precision: 24.84 | recall: 32.50 | f1: 28.15 | f1_macro: 62.29
[DEV]   accuracy: 93.41 | precision: 23.67 | recall: 33.20 | f1: 27.64 | f1_macro: 62.09
----------------------------------------------------------------------------------------
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec

Total number of UMLS partitions:  2
              precision    recall  f1-score   support

           0       0.97      0.97      0.97     49644
           1       0.50      0.58      0.54      2938

    accuracy                           0.94     52582
   macro avg       0.74      0.77      0.75     52582
weighted avg       0.95      0.94      0.95     52582

Total number of UMLS partitions:  2
              precision    recall  f1-score   support

           0       0.95      0.96      0.96     48338
           1       0.38      0.36      0.37      3446

    accuracy                           0.92     51784
   macro avg       0.67      0.66      0.66     51784
weighted avg       0.92      0.92      0.92     51784

Total number of UMLS partitions:  2
              precision    recall  f1-score   support

           0       0.93      0.96      0.95     46943
           1       0.45      0.30      0.36      4841

    accuracy                           0.90     51784
   macro avg       0

In [ ]:
predicted_i = train(partitioned_i_umls_fuzzy, train_i_candidates, test_i_ebm_candidates, test_i_ebm_corr_candidates, Y_i, 'i', paramgrid = param_grid, mode = 'pred')

Hyperparamater Search Space: 336
Executing the experiment level:  UMLS
Total number of UMLS partitions:  3
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.18 | precision: 33.50 | recall: 12.61 | f1: 18.32 | f1_macro: 57.11
[DEV]   accuracy: 92.27 | precision: 32.79 | recall: 12.91 | f1: 18.53 | f1_macro: 57.23
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 90.32 | precision: 26.38 | recall: 21.90 | f1: 23.93 | f1_macro: 59.38
[DEV]   accuracy: 90.30 | precision: 25.29 | recall: 21.73 | f1: 23.37 | f1_macro: 59.10
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model


[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 90.37 | precision: 26.30 | recall: 21.33 | f1: 23.56 | f1_macro: 59.21
[DEV]   accuracy: 90.36 | precision: 25.23 | recall: 21.19 | f1: 23.04 | f1_macro: 58.95
----------------------------------------------------------------------------------------
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Mo

[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
Label model predicted -1 (TODO: this happens inconsistently)
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.5

[TRAIN] accuracy: 91.22 | precision: 27.79 | recall: 16.36 | f1: 20.59 | f1_macro: 57.97
[DEV]   accuracy: 91.22 | precision: 26.48 | recall: 16.35 | f1: 20.22 | f1_macro: 57.79
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 91.33 | precision: 28.38 | recall: 16.16 | f1: 20.59 | f1_macro: 58.00
[DEV]   accuracy: 91.36 | precision: 27.18 | recall: 16.08 | f1: 20.20 | f1_macro: 57.82
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 91.08 | precision: 29.13 | recall: 19.67 | f1: 23.49 | f1_macro: 59.38
[DEV]   accuracy: 91.07 | precision: 27.85 | recall: 19.61 | f1: 23.02 | f1_macro: 59.14
------

[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.5917916354520188
Best overall configuration:  {'lr': 0.0001, '

...

[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6082601583337462
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  50
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.55 | precision: 16.65 | recall: 44.84 | f1: 24.28 | f1_macro: 56.56
[DEV]   ac

[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 90.03 | precision: 25.74 | recall: 22.96 | f1: 24.27 | f1_macro: 59.47
[DEV]   accuracy: 90.22 | precision: 25.68 | recall: 23.11 | f1: 24.33 | f1_macro: 59.55
----------------------------------------------------------------------------------------
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.73 | precision: 22.81 | recall: 38.08 | f1: 28.53 | f1_macro: 60.61
[DEV]   accuracy: 86.84 | precision: 22.26 | recall: 37.45 | f1: 27.92 | f1_macro: 60.34
------

Best overall macro F1 score:  0.6082601583337462
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  55
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.46 | precision: 16.59 | recall: 44.91 | f1: 24.23 | f1_macro: 56.51
[DEV]   accuracy: 80.42 | precision: 16.10 | recall: 44.59 | f1: 23.66 | f1_macro: 56.21
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.05 | precision: 18.93 | recall: 43.75 | f1: 26.42 | f1_macro: 58.42
[DEV]   accuracy: 82.99 | precision: 18.31 | recall: 43.33 | f1: 25.74 | f1_macro: 58.07


[TRAIN] accuracy: 90.03 | precision: 25.70 | recall: 22.92 | f1: 24.23 | f1_macro: 59.45
[DEV]   accuracy: 90.22 | precision: 25.71 | recall: 23.15 | f1: 24.36 | f1_macro: 59.57
----------------------------------------------------------------------------------------
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.72 | precision: 22.81 | recall: 38.08 | f1: 28.53 | f1_macro: 60.61
[DEV]   accuracy: 86.84 | precision: 22.25 | recall: 37.44 | f1: 27.91 | f1_macro: 60.33
----------------------------------------------------------------------------------------
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[

[TRAIN] accuracy: 80.45 | precision: 16.59 | recall: 44.93 | f1: 24.23 | f1_macro: 56.50
[DEV]   accuracy: 80.41 | precision: 16.09 | recall: 44.59 | f1: 23.65 | f1_macro: 56.21
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.02 | precision: 18.89 | recall: 43.76 | f1: 26.39 | f1_macro: 58.40
[DEV]   accuracy: 82.96 | precision: 18.28 | recall: 43.33 | f1: 25.71 | f1_macro: 58.05
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.66 | precision: 20.54 | recall: 47.01 | f1: 28.58 | f1_macro: 59.68
[DEV]   accuracy: 83.76 | precision: 20.10 | recall: 46.59 | f1: 28.09 | f1_macro: 59.47
------

In [ ]:
# data_df.p.to_numpy() , # 0 -7
# data_df.p_f.to_numpy() , # 1 -6
# test_ebm_data.p.to_numpy() , # 2 -5
# test_ebm_data.p_f.to_numpy() , # 3 -4
# test_physio_data.p.to_numpy(),  # 4 -3
# test_ebm_corr_df.p.to_numpy(),   # 5 -2
# test_ebm_corr_df.p_f.to_numpy() # 6 -1

In [70]:
# EBM PICO corrected test labels (no LFs dropped) - New ReGeX, Abbreviation dictionaries added


predicted_p = train(partitioned_p_umls_fuzzy, train_candidates, test_candidates, Y_p, 'p', paramgrid = param_grid, testname = 'test_ebm_correct')

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.01 | precision: 25.95 | recall: 24.90 | f1: 25.42 | f1_macro: 61.15
[DEV]   accuracy: 94.24 | precision: 24.73 | recall: 25.46 | f1: 25.09 | f1_macro: 61.05
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.27 | precision: 28.10 | recall: 25.64 | f1: 26.81 | f1_macro: 61.91
[DEV]   accuracy: 94.49 | precision: 26.75 | recall: 26.18 | f1: 26.46 | f1_macro: 61.80
----------------------------------------------------------------

[16] Label Model
[17] Label Model
[18] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.00 | precision: 25.39 | recall: 36.51 | f1: 29.95 | f1_macro: 63.13
[DEV]   accuracy: 93.14 | precision: 23.89 | recall: 37.07 | f1: 29.05 | f1_macro: 62.72
----------------------------------------------------------------------------------------
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.000

[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.96 | precision: 24.86 | recall: 35.56 | f1: 29.27 | f1_macro: 62.78
[DEV]   accuracy: 93.14 | precision: 23.61 | recall: 36.24 | f1: 28.59 | f1_macro: 62.49
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.91 | precision: 24.83 | recall: 36.10 | f1: 29.42 | f1_macro: 62.84
[DEV]   accuracy: 93.09 | precision: 23.55 | recall: 36.70 | f1: 28.69 | f1_macro: 62.53
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model

[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.99 | precision: 23.86 | recall: 32.44 | f1: 27.50 | f1_macro: 61.91
[DEV]   accuracy: 93.18 | precision: 22.85 | recall: 33.65 | f1: 27.22 | f1_macro: 61.82
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.87 | precision: 24.74 | recall: 36.27 | f1: 29.42 | f1_macro: 62.83
[DEV]   accuracy: 93.06 | precision: 23.66 | recall: 37.35 | f1: 28.97 | f1_macro: 62.66
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[1

Total number of UMLS partitions:  12
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.03 | precision: 21.29 | recall: 35.05 | f1: 26.49 | f1_macro: 61.14
[DEV]   accuracy: 92.23 | precision: 20.39 | recall: 36.15 | f1: 26.07 | f1_macro: 60.99
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.26 | precision: 21.85 | recall: 34.49 | f1: 26.76 | f1_macro: 61.34
[DEV]   accuracy: 92.42 | precision: 20.83 | recall: 35.68 | f1: 26.30 | f1_macro: 61.15
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_ini

...

[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  118
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}


[TRAIN] accuracy: 92.70 | precision: 22.69 | recall: 32.51 | f1: 26.72 | f1_macro: 61.44
[DEV]   accuracy: 92.82 | precision: 21.36 | recall: 33.33 | f1: 26.04 | f1_macro: 61.13
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.62 | precision: 22.52 | recall: 32.87 | f1: 26.73 | f1_macro: 61.42
[DEV]   accuracy: 92.78 | precision: 21.47 | recall: 34.08 | f1: 26.35 | f1_macro: 61.27
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.46 | precision: 22.80 | recal

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.42 | precision: 24.97 | recall: 30.26 | f1: 27.36 | f1_macro: 61.96
[DEV]   accuracy: 93.64 | precision: 23.83 | recall: 30.93 | f1: 26.92 | f1_macro: 61.80
----------------------------------------------------------------------------------------
[12] Label Model
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.78 | precision: 26.35 | recall: 28.87 | f1: 27.55 | f1_macro: 62.15
[DEV]   accuracy: 93.98 | precision: 25.00 | recall: 29.40 | f1: 27.02 | f1_macro: 61.94
----------------------------------------------------------------------------------------
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 

[TRAIN] accuracy: 93.21 | precision: 24.84 | recall: 32.50 | f1: 28.15 | f1_macro: 62.29
[DEV]   accuracy: 93.41 | precision: 23.67 | recall: 33.20 | f1: 27.64 | f1_macro: 62.09
----------------------------------------------------------------------------------------
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec

Total number of UMLS partitions:  127
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.70 | precision: 22.69 | recall: 32.51 | f1: 26.72 | f1_macro: 61.44
[DEV]   accuracy: 92.82 | precision: 21.36 | recall: 33.33 | f1: 26.04 | f1_macro: 61.13
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.62 | precision: 22.52 | recall: 32.87 | f1: 26.73 | f1_macro: 61.42
[DEV]   accuracy: 92.78 | precision: 21.47 | recall: 34.08 | f1: 26.35 | f1_macro: 61.27
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9

In [71]:
# EBM PICO original test (no LFs dropped) - New ReGeX, Abbreviation dictionaries added

predicted_p = train(partitioned_p_umls_fuzzy, train_candidates, test_ebm_candidates, Y_p, 'p', paramgrid = param_grid, testname = 'test_ebm')

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.01 | precision: 25.95 | recall: 24.90 | f1: 25.42 | f1_macro: 61.15
[DEV]   accuracy: 94.24 | precision: 24.73 | recall: 25.46 | f1: 25.09 | f1_macro: 61.05
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.27 | precision: 28.10 | recall: 25.64 | f1: 26.81 | f1_macro: 61.91
[DEV]   accuracy: 94.49 | precision: 26.75 | recall: 26.18 | f1: 26.46 | f1_macro: 61.80
----------------------------------------------------------------

[16] Label Model
[17] Label Model
[18] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.00 | precision: 25.39 | recall: 36.51 | f1: 29.95 | f1_macro: 63.13
[DEV]   accuracy: 93.14 | precision: 23.89 | recall: 37.07 | f1: 29.05 | f1_macro: 62.72
----------------------------------------------------------------------------------------
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.000

[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.96 | precision: 24.86 | recall: 35.56 | f1: 29.27 | f1_macro: 62.78
[DEV]   accuracy: 93.14 | precision: 23.61 | recall: 36.24 | f1: 28.59 | f1_macro: 62.49
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.91 | precision: 24.83 | recall: 36.10 | f1: 29.42 | f1_macro: 62.84
[DEV]   accuracy: 93.09 | precision: 23.55 | recall: 36.70 | f1: 28.69 | f1_macro: 62.53
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model

[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.99 | precision: 23.86 | recall: 32.44 | f1: 27.50 | f1_macro: 61.91
[DEV]   accuracy: 93.18 | precision: 22.85 | recall: 33.65 | f1: 27.22 | f1_macro: 61.82
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.87 | precision: 24.74 | recall: 36.27 | f1: 29.42 | f1_macro: 62.83
[DEV]   accuracy: 93.06 | precision: 23.66 | recall: 37.35 | f1: 28.97 | f1_macro: 62.66
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[1

Total number of UMLS partitions:  12
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.03 | precision: 21.29 | recall: 35.05 | f1: 26.49 | f1_macro: 61.14
[DEV]   accuracy: 92.23 | precision: 20.39 | recall: 36.15 | f1: 26.07 | f1_macro: 60.99
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.26 | precision: 21.85 | recall: 34.49 | f1: 26.76 | f1_macro: 61.34
[DEV]   accuracy: 92.42 | precision: 20.83 | recall: 35.68 | f1: 26.30 | f1_macro: 61.15
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_ini

...

[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  118
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}


[TRAIN] accuracy: 92.70 | precision: 22.69 | recall: 32.51 | f1: 26.72 | f1_macro: 61.44
[DEV]   accuracy: 92.82 | precision: 21.36 | recall: 33.33 | f1: 26.04 | f1_macro: 61.13
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.62 | precision: 22.52 | recall: 32.87 | f1: 26.73 | f1_macro: 61.42
[DEV]   accuracy: 92.78 | precision: 21.47 | recall: 34.08 | f1: 26.35 | f1_macro: 61.27
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.46 | precision: 22.80 | recal

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.42 | precision: 24.97 | recall: 30.26 | f1: 27.36 | f1_macro: 61.96
[DEV]   accuracy: 93.64 | precision: 23.83 | recall: 30.93 | f1: 26.92 | f1_macro: 61.80
----------------------------------------------------------------------------------------
[12] Label Model
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.78 | precision: 26.35 | recall: 28.87 | f1: 27.55 | f1_macro: 62.15
[DEV]   accuracy: 93.98 | precision: 25.00 | recall: 29.40 | f1: 27.02 | f1_macro: 61.94
----------------------------------------------------------------------------------------
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 

[TRAIN] accuracy: 93.21 | precision: 24.84 | recall: 32.50 | f1: 28.15 | f1_macro: 62.29
[DEV]   accuracy: 93.41 | precision: 23.67 | recall: 33.20 | f1: 27.64 | f1_macro: 62.09
----------------------------------------------------------------------------------------
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6275850899306384
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec

Total number of UMLS partitions:  127
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.70 | precision: 22.69 | recall: 32.51 | f1: 26.72 | f1_macro: 61.44
[DEV]   accuracy: 92.82 | precision: 21.36 | recall: 33.33 | f1: 26.04 | f1_macro: 61.13
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.62 | precision: 22.52 | recall: 32.87 | f1: 26.73 | f1_macro: 61.42
[DEV]   accuracy: 92.78 | precision: 21.47 | recall: 34.08 | f1: 26.35 | f1_macro: 61.27
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9

In [132]:
# EBM PICO corrected test labels (no LFs dropped)


predicted_p = train(partitioned_p_umls_fuzzy, train_candidates, test_candidates, Y_p, 'p', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.07 | precision: 25.60 | recall: 23.47 | f1: 24.49 | f1_macro: 60.70
[DEV]   accuracy: 94.31 | precision: 24.51 | recall: 24.10 | f1: 24.30 | f1_macro: 60.67
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 94.38 | precision: 27.29 | recall: 22.40 | f1: 24.60 | f1_macro: 60.84
[DEV]   accuracy: 94.62 | precision: 26.23 | recall: 23.14 | f1: 24.59 | f1_macro: 60.90
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] La

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.37 | precision: 25.86 | recall: 33.10 | f1: 29.04 | f1_macro: 62.78
[DEV]   accuracy: 93.54 | precision: 24.31 | recall: 33.31 | f1: 28.11 | f1_macro: 62.36
----------------------------------------------------------------------------------------
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Mod

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.73 | precision: 23.36 | recall: 33.95 | f1: 27.68 | f1_macro: 61.93
[DEV]   accuracy: 92.93 | precision: 22.34 | recall: 34.91 | f1: 27.24 | f1_macro: 61.76
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
[3] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.58 | precision: 23.20 | recall: 35.11 | f1: 27.94 | f1_macro: 62.01
[DEV]   accuracy: 92.76 | precision: 22.11 | recall: 36.05 | f1: 27.41 | f1_macro: 61.80
----------------------------------------------------------------------------------------
[4] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 600, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.72

[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 93.09 | precision: 24.89 | recall: 34.05 | f1: 28.76 | f1_macro: 62.56
[DEV]   accuracy: 93.28 | precision: 23.66 | recall: 34.76 | f1: 28.16 | f1_macro: 62.32
----------------------------------------------------------------------------------------
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.624993192237703
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  9
Grid search

[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6254031665399424
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UML

...

[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6254031665399424
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  59
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[

[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6254031665399424
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  61
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.15 | precision: 21.15 | recall: 33.62 | f1: 25.97 | f1_macro: 60.91
[DEV]   accuracy: 92.28 | precision: 20.15 | recall: 34.98 | f1: 25.57 | f1_macro: 60.75
--------------------------------------------

[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6254031665399424
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  63
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.15 | precision: 21.15 | recall: 33.62 | f1: 25.97 | f1_macro: 60.91
[DEV]   accuracy: 92.28 | precision: 20.15 | recall: 34.98 | f1: 25.57 | f1_macro: 60.75
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.31 | precision

Total number of UMLS partitions:  65
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.15 | precision: 21.15 | recall: 33.62 | f1: 25.97 | f1_macro: 60.91
[DEV]   accuracy: 92.28 | precision: 20.15 | recall: 34.98 | f1: 25.57 | f1_macro: 60.75
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.31 | precision: 21.69 | recall: 33.60 | f1: 26.36 | f1_macro: 61.15
[DEV]   accuracy: 92.46 | precision: 20.68 | recall: 34.88 | f1: 25.97 | f1_macro: 61.00
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adamax', 

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.31 | precision: 21.69 | recall: 33.60 | f1: 26.36 | f1_macro: 61.15
[DEV]   accuracy: 92.46 | precision: 20.68 | recall: 34.88 | f1: 25.97 | f1_macro: 61.00
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.31 | precision: 22.03 | recall: 34.50 | f1: 26.89 | f1_macro: 61.42
[DEV]   accuracy: 92.45 | precision: 20.92 | recall: 35.72 | f1: 26.38 | f1_macro: 61.20
----------------------------------------------------------------------------------------
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 92.

In [41]:
predicted_p = train(partitioned_p_umls_fuzzy, umls_p[1], nonumls_p[1], ds_p[1], heur_p[0], dict_p[1], Y_p, 'p', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  6
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.74 | precision: 45.10 | recall: 21.21 | f1: 28.85 | f1_macro: 60.77
[DEV]   accuracy: 86.79 | precision: 43.61 | recall: 20.79 | f1: 28.15 | f1_macro: 60.44
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.70 | precision: 36.04 | recall: 26.71 | f1: 30.68 | f1_macro: 61.04
[DEV]   accuracy: 84.73 | precision: 34.73 | recall: 25.70 | f1: 29.54 | f1_macro: 60.49
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] La

In [44]:
from sklearn.model_selection import train_test_split

predicted_p_series = pd.Series(predicted_p)
predicted_p_train , predicted_p_test  = [i.to_dict() for i in train_test_split(predicted_p_series, test_size=0.2, shuffle=False)]

In [46]:
with open('/mnt/nas2/results/Results/systematicReview/distant_pico/predictions/LabelModels/p/v4/bestmodel.tsv', 'w+') as wf:
    for k,v in predicted_p_test.items():
        string2write = str(k) + '\t' + str(v[0]) + '\t' + str(v[1]) + '\t' + str(v[2]) + '\t' + str(v[3]) + '\t' + str(v[4]) + '\n'
        wf.write(string2write)

In [297]:
# write the probablistic labels and the meta-data to file
tokens_write = np.array( [i[0] for i in predicted_p.values()]  )
series_write = Y = np.concatenate([series[0], series[1]])
part_of_speech_write = Y = np.concatenate([part_of_speech[0], part_of_speech[1]])
offsets_write = Y = np.concatenate([offsets[0], offsets[1]])
pred_proba_p_labels_write = [ i[1] for i in predicted_p.values() ]

In [298]:
Y_p_gold_write = np.concatenate([Y_p[0], Y_p[1]])

corpus_df = pd.DataFrame(data=[series_write, tokens_write, part_of_speech_write, offsets_write, pred_proba_p_labels_write, Y_p[0], Y_p[1]]).T
corpus_df.columns =['series', 'tokens', 'pos', 'offsets', 'pred_probas', 'true_labels', 'true_labels_fine']

In [300]:
series_set = list(set(corpus_df.series))

tokens = list(corpus_df.tokens)
offsets = list(corpus_df.offsets)
pos = list(corpus_df.pos)
pred_probas = list(corpus_df.pred_probas)
true_labels = list(corpus_df.true_labels)
true_labels_fine = list(corpus_df.true_labels_fine)


tokens_nest = []
offsets_nest = []
pos_nest = []
pred_probas_nest = []
true_labels_nest = []
true_labels_fine_nest = []

for series_i in series_set:

    indices = [i for i, x in enumerate( list( corpus_df.series ) ) if x == series_i]

    tokens_nest.append( tokens[ indices[0] : indices[-1]+1 ] )
    offsets_nest.append( offsets[ indices[0] : indices[-1]+1 ] )
    pos_nest.append( pos[ indices[0] : indices[-1]+1 ] )
    pred_probas_nest.append( pred_probas[ indices[0] : indices[-1]+1 ] )
    true_labels_nest.append( true_labels[ indices[0] : indices[-1]+1 ] )
    true_labels_fine_nest.append( true_labels_fine[ indices[0] : indices[-1]+1 ] )

In [301]:
write_p_df = pd.DataFrame(data=[tokens_nest, pos_nest, offsets_nest, pred_probas_nest, true_labels_nest, true_labels_fine_nest]).T
write_p_df.columns = ['tokens', 'pos', 'offsets', 'labels', 'true_labels', 'true_labels_fine']

write_p_df.to_csv(f'/mnt/nas2/results/Results/systematicReview/distant_pico/predictions/LabelModels/p/v4/bestmodel.tsv', sep='\t', encoding='utf-8', header='true')

token_list = [num for sublist in tokens_nest for num in sublist]
pred_probas_list = [num for sublist in pred_probas_nest for num in sublist]
pred_list = [np.argmax(np.asarray(num)) for sublist in pred_probas_nest for num in sublist]
true_list = [num for sublist in true_labels_nest for num in sublist]
true_fine_list = [num for sublist in true_labels_fine_nest for num in sublist]

ea_p_df = pd.DataFrame(data=[token_list, pred_probas_list, pred_list, true_list, true_fine_list]).T
ea_p_df.columns = ['tokens', 'label_probas', 'labels', 'true_labels', 'true_labels_fine']
_, val_ea_p_df = train_test_split(ea_p_df, test_size=0.2, shuffle=False)


val_ea_p_df.to_csv(f'/mnt/nas2/results/Results/systematicReview/distant_pico/predictions/LabelModels/p/v4/bestmodel_ea.tsv', sep='\t', encoding='utf-8', header='true')

In [81]:
# Executing on the lfs after dropping those LFs that did not label any token with positive label

train(partitioned_p_umls_fuzzy, umls_p[1], nonumls_p[1], ds_p[1], heur_p[0], dict_p[1], Y_p, 'p', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.14 | precision: 32.03 | recall: 29.45 | f1: 30.69 | f1_macro: 60.55
[DEV]   accuracy: 83.15 | precision: 30.97 | recall: 28.68 | f1: 29.78 | f1_macro: 60.11
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.39 | precision: 32.59 | recall: 29.04 | f1: 30.72 | f1_macro: 60.64
[DEV]   accuracy: 83.40 | precision: 31.53 | recall: 28.37 | f1: 29.87 | f1_macro: 60.23
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] La

Best overall macro F1 score:  0.6149199150790146
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  4
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.97 | precision: 31.52 | recall: 29.34 | f1: 30.39 | f1_macro: 60.34
[DEV]   accuracy: 82.97 | precision: 30.48 | recall: 28.62 | f1: 29.52 | f1_macro: 59.92
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.44 | precision: 38.94 | recall: 26.24 | f1: 31.35 | f1_macro: 61.60
[DEV]   accuracy: 85.43 | precision: 37.49 | recall: 25.38 | f1: 30.27 | f1_macro: 61.07
----

[TRAIN] accuracy: 86.47 | precision: 43.84 | recall: 23.98 | f1: 31.00 | f1_macro: 61.75
[DEV]   accuracy: 86.48 | precision: 42.27 | recall: 23.30 | f1: 30.04 | f1_macro: 61.28
----------------------------------------------------------------------------------------
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'see

[TRAIN] accuracy: 85.29 | precision: 38.19 | recall: 25.99 | f1: 30.93 | f1_macro: 61.35
[DEV]   accuracy: 85.29 | precision: 36.79 | recall: 25.21 | f1: 29.92 | f1_macro: 60.85
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.26 | precision: 42.53 | recall: 24.01 | f1: 30.69 | f1_macro: 61.53
[DEV]   accuracy: 86.25 | precision: 40.83 | recall: 23.04 | f1: 29.46 | f1_macro: 60.92
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.17 | precision: 42.14 | recall: 24

[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.0001, 'n_epochs': 600, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6149199150790146
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  12
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer

...

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.18 | precision: 34.69 | recall: 28.10 | f1: 31.05 | f1_macro: 61.06
[DEV]   accuracy: 84.20 | precision: 33.56 | recall: 27.38 | f1: 30.15 | f1_macro: 60.62
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.26 | precision: 42.49 | recall: 23.81 | f1: 30.52 | f1_macro: 61.45
[DEV]   accuracy: 86.27 | precision: 40.93 | recall: 22.98 | f1: 29.43 | f1_macro: 60.91
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.21 

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.18 | precision: 34.70 | recall: 28.12 | f1: 31.06 | f1_macro: 61.07
[DEV]   accuracy: 84.20 | precision: 33.58 | recall: 27.40 | f1: 30.18 | f1_macro: 60.64
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.25 | precision: 42.39 | recall: 23.65 | f1: 30.36 | f1_macro: 61.37
[DEV]   accuracy: 86.26 | precision: 40.83 | recall: 22.81 | f1: 29.27 | f1_macro: 60.83
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.07 

[TRAIN] accuracy: 86.26 | precision: 42.72 | recall: 24.78 | f1: 31.36 | f1_macro: 61.86
[DEV]   accuracy: 86.24 | precision: 41.11 | recall: 24.16 | f1: 30.43 | f1_macro: 61.40
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.25 | precision: 42.71 | recall: 24.78 | f1: 31.37 | f1_macro: 61.86
[DEV]   accuracy: 86.24 | precision: 41.12 | recall: 24.17 | f1: 30.44 | f1_macro: 61.40
----------------------------------------------------------------------------------------
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[2

[TRAIN] accuracy: 83.29 | precision: 32.26 | recall: 29.00 | f1: 30.54 | f1_macro: 60.52
[DEV]   accuracy: 83.31 | precision: 31.27 | recall: 28.34 | f1: 29.73 | f1_macro: 60.13
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.18 | precision: 34.70 | recall: 28.12 | f1: 31.06 | f1_macro: 61.07
[DEV]   accuracy: 84.20 | precision: 33.57 | recall: 27.40 | f1: 30.18 | f1_macro: 60.63
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.06 | precision: 41.65 | recall: 24.98 | f1: 31.23 | f1_macro: 61.73
[DEV]   accuracy: 86.05 | precision: 40.15 |

[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6149199150790146
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}


In [82]:
train(partitioned_i_umls_fuzzy, umls_i[1], nonumls_i[1], ds_i[1], heur_i[0], dict_i[1], Y_i, 'i', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.78 | precision: 26.80 | recall: 32.40 | f1: 29.34 | f1_macro: 60.40
[DEV]   accuracy: 84.95 | precision: 25.69 | recall: 32.45 | f1: 28.68 | f1_macro: 60.13
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.23 | precision: 29.91 | recall: 30.69 | f1: 30.30 | f1_macro: 61.33
[DEV]   accuracy: 86.40 | precision: 28.58 | recall: 30.57 | f1: 29.55 | f1_macro: 61.01
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] La

Best overall macro F1 score:  0.6169453364972467
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  4
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.18 | precision: 25.93 | recall: 33.52 | f1: 29.24 | f1_macro: 60.17
[DEV]   accuracy: 84.28 | precision: 24.76 | recall: 33.64 | f1: 28.53 | f1_macro: 59.85
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.53 | precision: 30.86 | recall: 30.76 | f1: 30.81 | f1_macro: 61.67
[DEV]   accuracy: 86.74 | precision: 29.61 | recall: 30.61 | f1: 30.10 | f1_macro: 61.39
-----

[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6179924952878891
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  7
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.20 | precision: 27.95 | recall: 32.78 | f1: 30.17 | f1_macro: 60.95
[DEV]   accuracy: 85.30 | precision: 26.59 | recall: 32.75 | f1: 29.35 | f1_macro: 60.57
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001

[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 87.92 | precision: 35.06 | recall: 28.05 | f1: 31.16 | f1_macro: 62.27
[DEV]   accuracy: 88.19 | precision: 33.87 | recall: 27.96 | f1: 30.63 | f1_macro: 62.09
----------------------------------------------------------------------------------------
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[4

[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.75 | precision: 29.83 | recall: 34.13 | f1: 31.83 | f1_macro: 61.94
[DEV]   accuracy: 85.96 | precision: 28.77 | recall: 34.24 | f1: 31.26 | f1_macro: 61.72
----------------------------------------------------------------------------------------
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 88.30 | precision: 36.24 | recall: 26.30 | f1: 30.48 | f1_macro: 62.05
[DEV]   accuracy: 88.59 | precision: 35.08 | recall: 26.32 | f1: 30.07 | f1_macro: 61.93
------

...

[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6215787900982248
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  58
Gr

Total number of UMLS partitions:  61
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.59 | precision: 25.19 | recall: 39.86 | f1: 30.87 | f1_macro: 60.46
[DEV]   accuracy: 82.65 | precision: 24.11 | recall: 40.07 | f1: 30.10 | f1_macro: 60.10
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.86 | precision: 29.27 | recall: 31.75 | f1: 30.46 | f1_macro: 61.30
[DEV]   accuracy: 85.95 | precision: 27.77 | recall: 31.63 | f1: 29.58 | f1_macro: 60.89
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'co

{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.82 | precision: 29.97 | recall: 33.98 | f1: 31.85 | f1_macro: 61.97
[DEV]   accuracy: 86.03 | precision: 28.81 | recall: 33.91 | f1: 31.15 | f1_macro: 61.69
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39

[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6215787900982248
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  68
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.18 | precision: 24.63 | recall: 40.13 | f1: 30.52 | f1_macro: 60.15
[DEV]   accuracy: 82.22 | precision: 23.55 | recall: 40.35 | f1: 29.74 | f1_macro: 

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.86 | precision: 29.27 | recall: 31.75 | f1: 30.46 | f1_macro: 61.30
[DEV]   accuracy: 85.95 | precision: 27.77 | recall: 31.63 | f1: 29.57 | f1_macro: 60.89
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.86 | precision: 29.90 | recall: 33.45 | f1: 31.57 | f1_macro: 61.84
[DEV]   accuracy: 86.08 | precision: 28.79 | recall: 33.42 | f1: 30.93 | f1_macro: 61.60
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15

In [83]:
train(partitioned_o_umls_fuzzy, umls_o[1], nonumls_o[1], ds_o[1], heur_o[0], dict_o[1], Y_o, 'o', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.21 | precision: 26.32 | recall: 13.29 | f1: 17.66 | f1_macro: 54.77
[DEV]   accuracy: 85.25 | precision: 27.26 | recall: 13.67 | f1: 18.21 | f1_macro: 55.05
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.74 | precision: 25.70 | recall: 32.47 | f1: 28.69 | f1_macro: 58.78
[DEV]   accuracy: 80.85 | precision: 26.41 | recall: 33.28 | f1: 29.45 | f1_macro: 59.19
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0

Best overall macro F1 score:  0.5957373728245161
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  4
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 79.71 | precision: 24.64 | recall: 34.00 | f1: 28.57 | f1_macro: 58.38
[DEV]   accuracy: 79.78 | precision: 25.18 | recall: 34.70 | f1: 29.18 | f1_macro: 58.69
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.70 | precision: 26.72 | recall: 30.60 | f1: 28.53 | f1_macro: 59.02
[DEV]   accuracy: 81.79 | precision: 27.31 | recall: 31.10 | f1: 29.08 | f1_macro: 59.32
-----

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.27 | precision: 26.09 | recall: 31.04 | f1: 28.35 | f1_macro: 58.79
[DEV]   accuracy: 81.38 | precision: 26.71 | recall: 31.56 | f1: 28.93 | f1_macro: 59.11
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.81 | precision: 28.30 | recall: 28.73 | f1: 28.51 | f1_macro: 59.37
[DEV]   accuracy: 82.93 | precision: 29.07 | recall: 29.29 | f1: 29.18 | f1_macro: 59.73
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model


[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.601382411721663
Best overall configuration:  {'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  10
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 77.00 | precision: 22.34 | recall: 37.42 | f1: 27.97 | f1_macro: 57.15
[DEV]   accuracy: 77.04 | precision: 22.80 | recall: 38.21 | f1: 28.56 | f1_macro: 57.44
------------------------------

[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.04 | precision: 29.09 | recall: 29.28 | f1: 29.18 | f1_macro: 59.77
[DEV]   accuracy: 83.02 | precision: 29.48 | recall: 29.76 | f1: 29.62 | f1_macro: 59.98
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model


...

[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.89 | precision: 28.86 | recall: 29.61 | f1: 29.23 | f1_macro: 59.75
[DEV]   accuracy: 82.89 | precision: 29.31 | recall: 30.11 | f1: 29.70 | f1_macro: 59.98
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label 

[TRAIN] accuracy: 80.94 | precision: 25.73 | recall: 31.65 | f1: 28.39 | f1_macro: 58.70
[DEV]   accuracy: 81.03 | precision: 26.35 | recall: 32.30 | f1: 29.02 | f1_macro: 59.04
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.88 | precision: 28.86 | recall: 29.64 | f1: 29.25 | f1_macro: 59.75
[DEV]   accuracy: 82.88 | precision: 29.31 | recall: 30.16 | f1: 29.73 | f1_macro: 59.99
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model


[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
Label model predicted -1 (TODO: this happens inconsistently)
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6014635647000673
Best overall configuration:  {'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  67
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 76.98 | precision: 22.3

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 77.19 | precision: 22.41 | recall: 36.98 | f1: 27.90 | f1_macro: 57.18
[DEV]   accuracy: 77.23 | precision: 22.86 | recall: 37.72 | f1: 28.47 | f1_macro: 57.47
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.17 | precision: 26.48 | recall: 27.79 | f1: 27.12 | f1_macro: 58.48
[DEV]   accuracy: 82.19 | precision: 26.84 | recall: 27.99 | f1: 27.40 | f1_macro: 58.63
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.50 

{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 78.31 | precision: 24.58 | recall: 39.52 | f1: 30.31 | f1_macro: 58.73
[DEV]   accuracy: 78.30 | precision: 24.85 | recall: 39.86 | f1: 30.61 | f1_macro: 58.88
----------------------------------------------------------------------------------------
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.87 | precision: 28.85 | recall: 29.68 | f1: 29.26 | f1_macro: 59.76
[DEV]   accuracy: 82.86 | precision: 29.30 | recall: 30.24 | f1: 29.76 | f1_macro: 60.00
----------------------------------------------------------------------------------------
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label M

In [161]:
train(partitioned_p_umls_fuzzy, umls_p[1], nonumls_p[1], ds_p[1], heur_p[0], dict_p[1], Y_p, 'p', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.16 | precision: 32.02 | recall: 29.29 | f1: 30.60 | f1_macro: 60.51
[DEV]   accuracy: 83.19 | precision: 31.01 | recall: 28.54 | f1: 29.72 | f1_macro: 60.09
----------------------------------------------------------------------------------------
[1] Label Model
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.41 | precision: 32.57 | recall: 28.87 | f1: 30.61 | f1_macro: 60.59
[DEV]   accuracy: 83.44 | precision: 31.57 | recall: 28.22 | f1: 29.80 | f1_macro: 60.20
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[

[TRAIN] accuracy: 85.43 | precision: 38.80 | recall: 25.86 | f1: 31.03 | f1_macro: 61.44
[DEV]   accuracy: 85.48 | precision: 37.61 | recall: 25.10 | f1: 30.11 | f1_macro: 61.00
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 87.21 | precision: 48.99 | recall: 21.27 | f1: 29.66 | f1_macro: 61.31
[DEV]   accuracy: 87.27 | precision: 47.49 | recall: 20.87 | f1: 29.00 | f1_macro: 61.00
----------------------------------------------------------------------------------------
[6] Label Model
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 87.01 | precision: 47.43 | recall: 22.86 | f1: 30.85 | f1_macro: 61.84
[DEV]   accuracy: 87.03 | pre

[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.45 | precision: 43.63 | recall: 23.73 | f1: 30.74 | f1_macro: 61.62
[DEV]   accuracy: 86.46 | precision: 42.09 | recall: 23.04 | f1: 29.78 | f1_macro: 61.14
----------------------------------------------------------------------------------------
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}


[TRAIN] accuracy: 83.45 | precision: 32.14 | recall: 27.49 | f1: 29.63 | f1_macro: 60.13
[DEV]   accuracy: 83.50 | precision: 31.35 | recall: 27.23 | f1: 29.14 | f1_macro: 59.90
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.70 | precision: 35.96 | recall: 26.58 | f1: 30.57 | f1_macro: 60.98
[DEV]   accuracy: 84.71 | precision: 34.76 | recall: 25.89 | f1: 29.68 | f1_macro: 60.55
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.81 | precision: 40.20 | recall: 24.55 | f1: 30.48 | f1_macro: 61.29
[DEV]   accuracy: 85.83 | precision: 38.76 | recall: 23.71 | f1: 29.42 | f1_macro: 60.77
------

[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6142796100146325
Best overall configuration:  {'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  11
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.44 | precision: 31.84 | recall: 26.88 | f1: 29.15 | f1_macro: 59.89
[DEV]   accuracy: 83.47 | precision: 30.92 | recall: 26.47 | f1: 28.52 | f1_macro: 59.59
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accurac

...

{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.15 | precision: 34.54 | recall: 27.95 | f1: 30.90 | f1_macro: 60.97
[DEV]   accuracy: 84.18 | precision: 33.46 | recall: 27.31 | f1: 30.07 | f1_macro: 60.57
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.70 | precision: 36.23 | recall: 27.23 | f1: 31.09 | f1_macro: 61.24
[DEV]   accuracy: 84.68 | precision: 34.90 | recall: 26.56 | f1: 30.17 | f1_macro: 60.78
----------------------------------------------------------------------------------------
[6] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN]

[TRAIN] accuracy: 86.83 | precision: 45.95 | recall: 22.01 | f1: 29.76 | f1_macro: 61.25
[DEV]   accuracy: 86.85 | precision: 44.27 | recall: 21.44 | f1: 28.89 | f1_macro: 60.82
----------------------------------------------------------------------------------------
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.01 | precision: 37.30 | recall: 26.81 | f1: 31.20 | f1_macro: 61.39
[DEV]   accuracy: 85.00 | precision: 35.98 | recall: 26.14 | f1: 30.28 | f1_macro: 60.94
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.38 | precision: 43.34 | recall: 24.16 | f1: 31.02 | f1_macro: 61.73
[DEV]   accuracy: 86.39 | precision: 41.76 | recall: 23.48 | 

[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6142796100146325
Best overall configuration:  {'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UML

Total number of UMLS partitions:  125
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.62 | precision: 33.05 | recall: 28.55 | f1: 30.63 | f1_macro: 60.67
[DEV]   accuracy: 83.68 | precision: 32.16 | recall: 27.93 | f1: 29.89 | f1_macro: 60.33
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.16 | precision: 34.55 | recall: 27.97 | f1: 30.92 | f1_macro: 60.98
[DEV]   accuracy: 84.18 | precision: 33.46 | recall: 27.31 | f1: 30.07 | f1_macro: 60.58
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_e

{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.67 | precision: 36.13 | recall: 27.27 | f1: 31.08 | f1_macro: 61.23
[DEV]   accuracy: 84.66 | precision: 34.85 | recall: 26.61 | f1: 30.17 | f1_macro: 60.78
----------------------------------------------------------------------------------------
[6] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.83 | precision: 45.91 | recall: 22.03 | f1: 29.77 | f1_macro: 61.25
[DEV]   accuracy: 86.84 | precision: 44.19 | recall: 21.47 | f1: 28.90 | f1_macro: 60.82
----------------------------------------------------------------------------------------
[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.99 | precision: 37.

In [ ]:
train(partitioned_i_umls_fuzzy, umls_i[1], nonumls_i[1], ds_i[1], heur_i[0], dict_i[1], Y_i, 'i', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.68 | precision: 26.86 | recall: 33.15 | f1: 29.67 | f1_macro: 60.54
[DEV]   accuracy: 84.89 | precision: 25.92 | recall: 33.40 | f1: 29.19 | f1_macro: 60.37
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.66 | precision: 31.10 | recall: 30.25 | f1: 30.67 | f1_macro: 61.65
[DEV]   accuracy: 86.91 | precision: 29.91 | recall: 30.07 | f1: 29.99 | f1_macro: 61.38
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
[

[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6174213629566849
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  4
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 84.68 | precision: 26.81 | recall: 32.98 | f1: 2

[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6188916272275283
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  7
(104

[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6220023610425133
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  10
(10

[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6229957875237966
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  13
(10

...

Best overall macro F1 score:  0.6229957875237966
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  89
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.77 | precision: 25.50 | recall: 39.89 | f1: 31.11 | f1_macro: 60.63
[DEV]   accuracy: 82.92 | precision: 24.57 | recall: 40.21 | f1: 30.51 | f1_macro: 60.38
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.45 | precision: 30.72 | recall: 31.07 | f1: 30.89 | f1_macro: 61.69
[DEV]   accuracy: 86.65 | precision: 29.49 | recall: 31.05 | f1: 30.25 | 

{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.28 | precision: 30.41 | recall: 31.57 | f1: 30.98 | f1_macro: 61.68
[DEV]   accuracy: 86.65 | precision: 29.85 | recall: 32.00 | f1: 30.89 | f1_macro: 61.75
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39

[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.6229957875237966
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  96
(1042460,)
(260616,)
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.70 | precis

{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.67 | precision: 25.36 | recall: 39.98 | f1: 31.03 | f1_macro: 60.56
[DEV]   accuracy: 82.81 | precision: 24.44 | recall: 40.32 | f1: 30.43 | f1_macro: 60.32
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.42 | precision: 30.81 | recall: 31.51 | f1: 31.16 | f1_macro: 61.81
[DEV]   accuracy: 86.61 | precision: 29.51 | recall: 31.39 | f1: 30.42 | f1_macro: 61.51
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 86.30 | precision: 30.46 | recall: 31.54

[TRAIN] accuracy: 86.30 | precision: 30.46 | recall: 31.53 | f1: 30.98 | f1_macro: 61.69
[DEV]   accuracy: 86.67 | precision: 29.89 | recall: 31.94 | f1: 30.88 | f1_macro: 61.75
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
[6] Label Model
[7] Label Model
[8] Label Model
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Labe

In [27]:
train(partitioned_o_umls_fuzzy, umls_o[1], nonumls_o[1], ds_o[1], heur_o[0], dict_o[1], Y_o, 'o', paramgrid = param_grid)

Hyperparamater Search Space: 336
Total number of UMLS partitions:  1
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 85.21 | precision: 26.32 | recall: 13.29 | f1: 17.66 | f1_macro: 54.77
[DEV]   accuracy: 85.25 | precision: 27.26 | recall: 13.67 | f1: 18.21 | f1_macro: 55.05
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.46 | precision: 25.12 | recall: 32.14 | f1: 28.20 | f1_macro: 58.44
[DEV]   accuracy: 80.55 | precision: 25.74 | recall: 32.86 | f1: 28.87 | f1_macro: 58.80
----------------------------------------------------------------------------------------
[2] Label Model
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0

Best overall macro F1 score:  0.5910333167877516
Best overall configuration:  {'lr': 0.001, 'l2': 0.0001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  4
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 79.51 | precision: 24.18 | recall: 33.56 | f1: 28.11 | f1_macro: 58.08
[DEV]   accuracy: 79.54 | precision: 24.65 | recall: 34.20 | f1: 28.65 | f1_macro: 58.35
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.08 | precision: 25.65 | recall: 30.83 | f1: 28.00 | f1_macro: 58.56
[DEV]   accuracy: 81.07 | precision: 26.05 | recall: 31.32 | f1: 28.44 | f1_macro: 58.77
-----

[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.5963771603561658
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  7
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 77.48 | precision: 22.48 | recall: 36.21 | f1: 27.74 | f1_macro: 57.20
[DEV]   accuracy: 77.50 | precision: 22.91 | recall: 36.92 | f1: 28.27 | f1_macro: 57.47
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimiz

[TRAIN] accuracy: 76.49 | precision: 21.68 | recall: 37.12 | f1: 27.38 | f1_macro: 56.68
[DEV]   accuracy: 76.51 | precision: 22.10 | recall: 37.87 | f1: 27.91 | f1_macro: 56.94
----------------------------------------------------------------------------------------
[1] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.9, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 80.10 | precision: 24.34 | recall: 31.64 | f1: 27.51 | f1_macro: 57.99
[DEV]   accuracy: 80.12 | precision: 24.81 | recall: 32.29 | f1: 28.06 | f1_macro: 58.26
----------------------------------------------------------------------------------------
[2] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.53 | precision: 25.68 | recall: 28.91 | f1: 27.20 | f1_macro: 58.31
[DEV]   accuracy: 81.51 | precision: 26.06 | recall: 29.36 | f1: 27.61 | f1_macro: 58.51
------

[7] Label Model
[8] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 82.54 | precision: 28.01 | recall: 29.49 | f1: 28.73 | f1_macro: 59.39
[DEV]   accuracy: 82.46 | precision: 28.32 | recall: 30.07 | f1: 29.17 | f1_macro: 59.58
----------------------------------------------------------------------------------------
[9] Label Model
[10] Label Model
[11] Label Model
[12] Label Model
[13] Label Model
Label model predicted -1 (TODO: this happens inconsistently)
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
Label model predicted -1 (TODO: this happ

...

{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 100, 'prec_init': 0.8, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.79 | precision: 25.32 | recall: 26.96 | f1: 26.11 | f1_macro: 57.86
[DEV]   accuracy: 81.78 | precision: 25.67 | recall: 27.27 | f1: 26.44 | f1_macro: 58.02
----------------------------------------------------------------------------------------
[3] Label Model
[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 79.22 | precision: 23.60 | recall: 33.13 | f1: 27.56 | f1_macro: 57.72
[DEV]   accuracy: 79.28 | precision: 24.13 | recall: 33.82 | f1: 28.17 | f1_macro: 58.03
----------------------------------------------------------------------------------------
[6] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 77.75

[4] Label Model
[5] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 700, 'prec_init': 0.6, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 79.21 | precision: 23.59 | recall: 33.14 | f1: 27.56 | f1_macro: 57.71
[DEV]   accuracy: 79.28 | precision: 24.12 | recall: 33.83 | f1: 28.16 | f1_macro: 58.03
----------------------------------------------------------------------------------------
[6] Label Model
{'lr': 0.0001, 'l2': 0.001, 'n_epochs': 200, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 77.75 | precision: 24.02 | recall: 39.95 | f1: 30.01 | f1_macro: 58.39
[DEV]   accuracy: 77.70 | precision: 24.28 | recall: 40.46 | f1: 30.35 | f1_macro: 58.54
----------------------------------------------------------------------------------------
[7] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.80

[TRAIN] accuracy: 77.74 | precision: 24.02 | recall: 39.99 | f1: 30.01 | f1_macro: 58.39
[DEV]   accuracy: 77.68 | precision: 24.28 | recall: 40.51 | f1: 30.36 | f1_macro: 58.54
----------------------------------------------------------------------------------------
[7] Label Model
{'lr': 0.001, 'l2': 0.001, 'n_epochs': 1000, 'prec_init': 0.9, 'optimizer': 'sgd', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 83.80 | precision: 28.72 | recall: 24.09 | f1: 26.21 | f1_macro: 58.55
[DEV]   accuracy: 83.78 | precision: 29.11 | recall: 24.41 | f1: 26.55 | f1_macro: 58.72
----------------------------------------------------------------------------------------
[8] Label Model
[9] Label Model
[10] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 81.38 | precision: 26.22 | recall: 30.91 | f1: 28.37 | f1_macro: 58.83
[DEV]   accuracy: 81.33 | precision: 26.61 | recall: 31.57 |

[12] Label Model
[13] Label Model
[14] Label Model
[15] Label Model
[16] Label Model
[17] Label Model
[18] Label Model
[19] Label Model
[20] Label Model
[21] Label Model
[22] Label Model
[23] Label Model
[24] Label Model
[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.5964504382266139
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 600, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UM

[25] Label Model
[26] Label Model
[27] Label Model
[28] Label Model
[29] Label Model
[30] Label Model
[31] Label Model
[32] Label Model
[33] Label Model
[34] Label Model
[35] Label Model
[36] Label Model
[37] Label Model
[38] Label Model
[39] Label Model
[40] Label Model
[41] Label Model
[42] Label Model
[43] Label Model
[44] Label Model
[45] Label Model
[46] Label Model
[47] Label Model
[48] Label Model
[49] Label Model
BEST
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 50, 'prec_init': 0.8, 'optimizer': 'adamax', 'lr_scheduler': 'constant', 'seed': 1234}
Best overall macro F1 score:  0.5964504382266139
Best overall configuration:  {'lr': 0.0001, 'l2': 0.001, 'n_epochs': 600, 'prec_init': 0.6, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
Total number of UMLS partitions:  126
Grid search over 50 configs
[0] Label Model
{'lr': 0.001, 'l2': 0.0001, 'n_epochs': 200, 'prec_init': 0.8, 'optimizer': 'adam', 'lr_scheduler': 'constant', 'seed': 1234}
[TRAIN] accuracy: 70.78 | preci

In [134]:
from os import listdir
from os.path import isfile, join
mypath_P = '/mnt/nas2/data/systematicReview/ebm_nlp_2_00/annotations/aggregated/starting_spans/participants/test/gold'
onlyfiles_P = [f for f in listdir(mypath_P) if isfile(join(mypath_P, f))]

mypath_I = '/mnt/nas2/data/systematicReview/ebm_nlp_2_00/annotations/aggregated/starting_spans/interventions/test/gold'
onlyfiles_I = [f for f in listdir(mypath_I) if isfile(join(mypath_I, f))]

mypath_O = '/mnt/nas2/data/systematicReview/ebm_nlp_2_00/annotations/aggregated/starting_spans/outcomes/test/gold'
onlyfiles_O = [f for f in listdir(mypath_O) if isfile(join(mypath_O, f))]

In [136]:
onlyfiles = onlyfiles_P + onlyfiles_I + onlyfiles_O

In [137]:
onlyfiles = list(set(onlyfiles))

In [144]:
onlyfiles_clean = [f.replace('.AGGREGATED.ann', '') for f in onlyfiles]

In [143]:
mydir = '/mnt/nas2/data/systematicReview/ebm_nlp_2_00/documents/'
all_docs = [f for f in listdir(mydir) if isfile(join(mydir, f))]

In [150]:
test_ebm = []

for count, d in enumerate(all_docs):
    if 'txt' in d and str(d).replace('.txt', '') in onlyfiles_clean:
        test_ebm.append(d)

In [ ]:
cp /mnt/nas2/data/systematicReview/ebm_nlp_2_00/documents/{22956006.txt,21718094.txt,11381289.txt,21393467.txt,23549581.txt,18189160.txt,23417625.txt,1780092.txt,8913901.txt,25886492.txt,8989009.txt,11891832.txt,2678230.txt,20189026.txt,2188766.txt,7827398.txt,8916620.txt,1968178.txt,11401641.txt,10752495.txt,23392542.txt,4919024.txt,3919804.txt,23114870.txt,15854186.txt,1131298.txt,8519720.txt,2908133.txt,7017018.txt,19096921.txt,2066441.txt,21029638.txt,20226474.txt,21982657.txt,21914768.txt,17616069.txt,24989854.txt,21170734.txt,18773733.txt,2223363.txt,10390665.txt,18229990.txt,24515505.txt,1459268.txt,17321989.txt,10934569.txt,10912743.txt,23103798.txt,19727232.txt,12709693.txt,15014018.txt,7844976.txt,9394106.txt,24075141.txt,8911223.txt,19108790.txt,3067745.txt,21491990.txt,9229602.txt,3081600.txt,9573502.txt,18783504.txt,11317090.txt,23356250.txt,21924760.txt,20618920.txt,19802506.txt,9695300.txt,23849147.txt,17293018.txt,18975051.txt,14763035.txt,24726342.txt,25784723.txt,25068497.txt,24350813.txt,20560622.txt,22435114.txt,22341427.txt,3074300.txt,10475150.txt,16055807.txt,18503531.txt,25950425.txt,22538329.txt,10070173.txt,24451919.txt,20147856.txt,8779382.txt,24660757.txt,10763172.txt,2224060.txt,23985254.txt,16505427.txt,2803397.txt,17897478.txt,15358868.txt,19159999.txt,21866656.txt,11229858.txt,25479285.txt,7707420.txt,16427787.txt,19301724.txt,10940525.txt,12960652.txt,12576806.txt,11642083.txt,6418441.txt,25931290.txt,7598243.txt,20739054.txt,8911222.txt,6951573.txt,14739125.txt,8771302.txt,2088233.txt,22416755.txt,11495215.txt,1286547.txt,7808649.txt,8726604.txt,24803369.txt,21211686.txt,10589810.txt,15193668.txt,24960665.txt,22420121.txt,24080592.txt,1963383.txt,25898782.txt,10764172.txt,18337284.txt,21975269.txt,3534803.txt,11454878.txt,24317958.txt,23021296.txt,22646975.txt,12586799.txt,22744141.txt,21669557.txt,19376304.txt,9481998.txt,22271197.txt,20509069.txt,6989377.txt,7814711.txt,10578479.txt,15133359.txt,7853069.txt,6938020.txt,18077611.txt,15848261.txt,6421395.txt,26278470.txt,15858959.txt,18845996.txt,12477021.txt,384815.txt,20943715.txt,23838728.txt,26210844.txt,21106663.txt,16295154.txt,18544974.txt,11829043.txt,22154769.txt,21896676.txt,1669598.txt,6920252.txt,19708562.txt,16167234.txt,7831628.txt,18958161.txt,12139812.txt,22897461.txt,22865017.txt,14679127.txt,9816035.txt,11737955.txt,361799.txt,12595499.txt,9730996.txt,25885649.txt,20804366.txt,25369243.txt,11750293.txt,22881991.txt,11099086.txt,23357440.txt} /mnt/nas2/data/systematicReview/ebm_nlp_2_00/test_ebm_docs

In [53]:
import re

In [79]:
(?x)(?(DEFINE)(?<one_to_9>(?:f(?:ive|our)|s(?:even|ix)|t(?:hree|wo)|(?:ni|o)ne|eight) )(?<ten_to_19>(?:(?:(?:s(?:even|ix)|f(?:our|if)|nine)te|e(?:ighte|lev))en|t(?:(?:hirte)?en|welve)))(?<two_digit_prefix>(?:s(?:even|ix)|t(?:hir|wen)|f(?:if|or)|eigh|nine)ty)(?<one_to_99>(?&two_digit_prefix)(?:[- ](?&one_to_9))?|(?&ten_to_19)|(?&one_to_9))(?<one_to_999>(?&one_to_9)[ ]hundred(?:[ ](?:and[ ])?(?&one_to_99))?|(?&one_to_99))(?<one_to_999_999>(?&one_to_999)[ ]thousand(?:[ ](?&one_to_999))?|(?&one_to_999))(?<one_to_999_999_999>(?&one_to_999)[ ]million(?:[ ](?&one_to_999_999))?|(?&one_to_999_999))(?<one_to_999_999_999_999>(?&one_to_999)[ ]billion(?:[ ](?&one_to_999_999_999))?|(?&one_to_999_999_999))(?<one_to_999_999_999_999_999>(?&one_to_999)[ ]trillion(?:[ ](?&one_to_999_999_999_999))?|(?&one_to_999_999_999_999))(?<bignumber>zero|(?&one_to_999_999_999_999_999))(?<zero_to_9>(?&one_to_9)|zero))

SyntaxError: invalid syntax (<ipython-input-79-5c7600719d46>, line 1)

In [74]:
sample_size_number = r'\b(?&one_to_999_999_999)\b'

In [75]:
compiled_pattern = re.compile(sample_size_number)

error: unknown extension ?& at position 3